In [ ]:
import pandas as pd
import altair as alt
import numpy as np

df1 = pd.read_csv('./TEPC_2015_Oct_eia.csv')
df2 = pd.read_csv('./TEPC_2020_Oct_eia.csv')
df3 = pd.read_csv('./TEPC_2025_Jan_eia.csv')

These files have overlapping dates, along with some nulls. However, the null fields have been filled with string markers. The duplicate dates will need to be dropped (unless they are different). The amount of nulls will determine how they are addressed.

In [ ]:
dfs = [df1, df2, df3]

combined = pd.concat(dfs, ignore_index=True)
combined["date_time"] = pd.to_datetime(combined["date_time"], errors="coerce")

df = (
    combined
    .sort_values("date_time")  # get everything in order
    .groupby("date_time", as_index=False)
    .agg(lambda s: s.dropna().iloc[0] if s.dropna().size > 0 else pd.NA)
)

In [ ]:
# drop forecast column, not needed and too many missing values
df.drop(columns=['forecast demand (MW)'], axis=1, inplace=True)

# convert demand columns to numeric 
df['demand (MW)'] = pd.to_numeric(df['demand (MW)'], errors='coerce')

# changing 'MISSING' to NaN
df.replace("MISSING", np.nan, inplace=True)
#df.isna().sum()

One column has been removed, due to lack of use and too many NaNs. The remaining missing values can be filled, either with a set value (mean), or a forward- or backwards-fill. Since the values follow a more stepped pattern (due to daily and monthly pattern changes), filling with a mean value would cause distortions rather than smoothly filling the gaps. Using the forward or backwards fill methods make more sense, as this will populate the NaNs with closer values.

In [ ]:
df.ffill(axis=0, inplace=True, limit_area='inside')
df.isna().sum()

date_time      0
demand (MW)    3
dtype: int64

In [ ]:
# extract year, month, and hour
df['year'] = df['date_time'].dt.year
df['month'] = df['date_time'].dt.month
df['hour'] = df['date_time'].dt.hour

A z-score can flag outliers that are far from any other values. Since their validity and cause cannot be determined, they should be dropped to prevent distortions.

In [ ]:
# Checking for outlier values that may be erroneous
df['zscore'] = (df['demand (MW)'] - df['demand (MW)'].rolling(24, min_periods=1).mean()) / df['demand (MW)'].rolling(24, min_periods=1).std()
outliers = df[np.abs(df['zscore']) > 3]  # flag points more than 3 std from local mean

In [ ]:
#outliers
# remove specific rows by index which are in the outliers
df.drop(labels=[0, 1, 2, 24303, 24977, 55969, 57899, 57901, 74835, 80004, 80251, 80762], axis=0, inplace=True)

In [ ]:
# save merged df
df.to_csv('./TEPC_demand_2015_2025.csv', index=False)

In [ ]:
def get_season(month):
    if month in [12, 1, 2]:
        return 'Winter'
    elif month in [3, 4, 5]:
        return 'Spring'
    elif month in [6, 7, 8]:
        return 'Summer'
    else:
        return 'Fall'

df['season'] = df['month'].apply(get_season)

In [ ]:
monthly_avg = df.groupby(['year', 'month'])['demand (MW)'].mean().reset_index()
monthly_avg.columns = ['year', 'month', 'avg_demand']

In [ ]:
# avg demand/hour/month/year
df_avg = (
    df.groupby(['year', 'month', 'hour'], as_index=False)['demand (MW)']
    .mean()
    .rename(columns={'demand (MW)': 'avg_demand_MW'})
)

# map month  names for readability
month_names = ['Jan','Feb','Mar','Apr','May','Jun','Jul','Aug','Sep','Oct','Nov','Dec']
df_avg['month_name'] = df_avg['month'].apply(lambda x: month_names[x-1])

In [ ]:
# Chart 1: Average Demand by Month Across Years
chart1 = alt.Chart(monthly_avg).mark_line(point=True).encode(
    x=alt.X('month:O', title='Month'),
    y=alt.Y('avg_demand:Q', title='Average Demand (MW)'),
    color=alt.Color('year:N', title='Year')
).properties(
    width=700,
    height=300,
    title='Average Demand by Month Across Years'
)

chart1.display()

alt.Chart(...)

In [ ]:
alt.data_transformers.disable_max_rows()

# Chart 3: Load Duration Curve
load_duration = df[['demand (MW)']].copy()
load_duration = load_duration.sort_values('demand (MW)', ascending=False).reset_index(drop=True)
load_duration['percentile'] = (load_duration.index / len(load_duration)) * 100
load_duration['hours'] = load_duration.index

chart3 = alt.Chart(load_duration).mark_area(line=True).encode(
    x=alt.X('percentile:Q', title='Percentage of Time (%)'),
    y=alt.Y('demand (MW):Q', title='Demand (MW)')
).properties(
    width=700,
    height=300,
    title='Load Duration Curve'
)

chart3.display()

alt.Chart(...)

In [ ]:
# Chart 4: Typical Day Profiles by Season
hourly_by_season = df.groupby(['season', 'hour'])['demand (MW)'].mean().reset_index()
hourly_by_season.columns = ['season', 'hour', 'avg_demand']

chart4 = alt.Chart(hourly_by_season).mark_line(point=True).encode(
    x=alt.X('hour:Q', title='Hour of Day', scale=alt.Scale(domain=[0, 23])),
    y=alt.Y('avg_demand:Q', title='Average Demand (MW)'),
    color=alt.Color('season:N', title='Season'),
).properties(
    width=700,
    height=300,
    title='Typical Day Profiles by Season'
)

chart4.display()

alt.Chart(...)

In [ ]:
# Chart 5: Average Hourly Electricity Demand per Month by Year
chart = (
    alt.Chart(df_avg)
    .mark_line(interpolate='monotone')
    .encode(
        x=alt.X('hour:O', title='Hour of Day'),
        y=alt.Y('avg_demand_MW:Q', title='Avg Demand (MW)').scale(domain=(500, 3500)),
        color=alt.Color('year:N', title='Year'),
    ).properties(
        title='Average Hourly Electricity Demand per Month by Year',
        width=200,
        height=150
    )
    .facet(
        facet=alt.Facet('month_name:N', title='Month', sort=month_names),
        columns=3
    )
    
)

chart.resolve_scale(y='independent')

alt.FacetChart(...)

In [ ]:
# Chart 6: Year-over-Year Comparison
chart2 = alt.Chart(monthly_avg).mark_bar().encode(
    x=alt.X('Month:O', title='Month'),
    y=alt.Y('avg_demand:Q', title='Average Demand (MW)'),
    color=alt.Color('Year:N', title='Year'),
    xOffset='Year:N'
).properties(
    width=700,
    height=300,
    title='Year-over-Year Monthly Comparison'
)

chart6.display()

In [ ]:
# Chart 7: Load Factor (Avg/Peak Demand Ratio)
load_factor = df.groupby(['Year', 'Month']).agg({
    'Ann_Arbor_Residential_MW': ['mean', 'max']
}).reset_index()
load_factor.columns = ['year', 'month', 'avg_demand', 'peak_demand']
load_factor['load_factor'] = (load_factor['avg_demand'] / load_factor['peak_demand']) * 100

chart5 = alt.Chart(load_factor).mark_bar().encode(
    x=alt.X('month:O', title='Month'),
    y=alt.Y('load_factor:Q', title='Load Factor (%)', scale=alt.Scale(domain=[0, 100])),
    color=alt.Color('year:N', title='Year'),
    xOffset='year:N'
).properties(
    width=700,
    height=300,
    title='Load Factor: System Utilization (Avg/Peak Demand)'
)

chart7.display()

In [ ]:
# repeat for Ann Arbor visuals